In [35]:
import numpy as np
import os
import cv2
from skimage.feature import local_binary_pattern
from skimage.color import rgb2gray

# LBP parameters
radius = 1  # Radius of LBP
n_points = 8 * radius  # Number of points in LBP

# Define the path to your dataset
dataset_path = r'C:\Users\venla\Documents\Affective_computing\Project\PreProcess Img\NI_Acropped\Dark'  # Replace with your actual dataset path

# Define the emotion labels and their corresponding numeric values
emotion_labels = {
    'Anger': 0,
    'Disgust': 1,
    'Fear': 2,
    'Happiness': 3,
    'Sadness': 4,
    'Surprise': 5
}

In [37]:



# Arrays to store images and corresponding labels
image_data = []
labels = []

# Supported image formats
supported_image_formats = ('.jpg', '.jpeg', '.png')

# Traverse the dataset folder
for subject_folder in os.listdir(dataset_path):
    subject_path = os.path.join(dataset_path, subject_folder)
    
    # Check if it's a directory
    if os.path.isdir(subject_path):
        # Traverse each emotion folder within each subject folder
        for emotion_folder in os.listdir(subject_path):
            emotion_path = os.path.join(subject_path, emotion_folder)
            
            # Check if it's a directory and corresponds to a valid emotion
            if os.path.isdir(emotion_path) and emotion_folder in emotion_labels:
                # Get the numeric label for the emotion
                label = emotion_labels[emotion_folder]
                

                emotion_data = []
                # Traverse all the files in the emotion folder
                for image_file in os.listdir(emotion_path):
                    # Only process files with valid image extensions
                    if image_file.endswith(supported_image_formats):
                        image_path = os.path.join(emotion_path, image_file)
                        
                        # Read the image
                        image = rgb2gray(cv2.imread(image_path))
                        
                        # Resize the image if necessary (e.g., to 224x224 or another size)
                        # image = cv2.resize(image, (224, 224))  # Optional step
                        
                        # Add the image and its label to the arrays
                        emotion_data.append(image)
                if len(emotion_data) > 0:      
                    image_data.append(emotion_data)
                    labels.append(label)
                        

# Convert image data and labels to NumPy arrays
image_data = np.array(image_data, dtype = object)
labels = np.array(labels)

print(f"Total images loaded: {len(image_data)}")
print(f"Total labels: {len(labels)}")


[[array([[0.51372549, 0.51764706, 0.52156863, ..., 0.38039216, 0.34117647,
        0.32941176],
       [0.51372549, 0.51764706, 0.51764706, ..., 0.37647059, 0.3372549 ,
        0.3254902 ],
       [0.50980392, 0.51372549, 0.51764706, ..., 0.38039216, 0.3372549 ,
        0.31764706],
       ...,
       [0.24705882, 0.28235294, 0.30588235, ..., 0.29411765, 0.2627451 ,
        0.19215686],
       [0.22745098, 0.26666667, 0.29411765, ..., 0.27843137, 0.24313725,
        0.16470588],
       [0.20784314, 0.25098039, 0.28627451, ..., 0.27058824, 0.22745098,
        0.14509804]]), array([[0.51372549, 0.51372549, 0.51764706, ..., 0.37647059, 0.34117647,
        0.33333333],
       [0.50980392, 0.51372549, 0.51764706, ..., 0.38431373, 0.34509804,
        0.32941176],
       [0.50588235, 0.50980392, 0.51372549, ..., 0.39215686, 0.34509804,
        0.32156863],
       ...,
       [0.24705882, 0.2745098 , 0.30196078, ..., 0.29803922, 0.27058824,
        0.2       ],
       [0.22745098, 0.25490196, 

In [38]:
# Function to compute LBP for a given plane
def compute_lbp(image, radius, n_points):
    return local_binary_pattern(image, n_points, radius, method='uniform')


In [45]:
#frames = np.array(frames)  # Convert to numpy array for easier manipulation
lbp_top_vectors = []
for video in image_data:
    video = np.array(video)
    # 1. LBP on XY plane (regular LBP on each frame)
    num_frames, height, width = video.shape
    xy_lbp_histograms = []

    for frame in video:
        lbp = compute_lbp(frame, radius, n_points)
        hist, _ = np.histogram(lbp.ravel(), bins=np.arange(0, n_points+3), density=True)
        hist = hist.astype(float) / hist.sum()
        xy_lbp_histograms.append(hist)

    xy_lbp_histograms = np.array(xy_lbp_histograms)
    xy_lbp_histogram = np.mean(xy_lbp_histograms, axis=0)  # Average histogram over all frames

    # 2. LBP on XT plane (variation along x-axis over time for all rows)
    xt_lbp_histograms = []
    for row in range(height):  # Iterate over each row
        xt_planes = video[:, row, :]  # Get XT plane for this row
        xt_lbp = compute_lbp(xt_planes, radius, n_points)
        hist, _ = np.histogram(xt_lbp.ravel(), bins=np.arange(0, n_points+3), density=True)
        hist = hist.astype(float) / hist.sum()
        xt_lbp_histograms.append(hist)

    xt_lbp_histograms = np.array(xt_lbp_histograms)
    xt_lbp_histogram = np.mean(xt_lbp_histograms, axis=0)  # Average histogram over all rows

    # 3. LBP on YT plane (variation along y-axis over time for all columns)
    yt_lbp_histograms = []
    for col in range(width):  # Iterate over each column
        yt_planes = video[:, :, col]  # Get YT plane for this column
        yt_lbp = compute_lbp(yt_planes, radius, n_points)
        hist, _ = np.histogram(yt_lbp.ravel(), bins=np.arange(0, n_points+3), density=True)
        hist = hist.astype(float) / hist.sum()
        yt_lbp_histograms.append(hist)

    yt_lbp_histograms = np.array(yt_lbp_histograms)
    yt_lbp_histogram = np.mean(yt_lbp_histograms, axis=0)  # Average histogram over all columns

    # Concatenate the histograms to form LBP-TOP feature vector
    lbp_top_vector = np.concatenate([xy_lbp_histogram, xt_lbp_histogram, yt_lbp_histogram])
    lbp_top_vectors.append(lbp_top_vector)
print(lbp_top_vectors)

C:\Users\venla\AppData\Roaming\Python\Python39\site-packages\skimage\feature\texture.py:360: UserWarning: Applying `local_binary_pattern` to floating-point images may give unexpected results when small numerical differences between adjacent pixels are present. It is recommended to use this function with images of integer dtype.
  warnings.warn(


[array([0.00964533, 0.03021189, 0.02812334, 0.14271284, 0.38607124,
       0.21948811, 0.05827447, 0.04540898, 0.03890028, 0.04116351,
       0.02334624, 0.04805954, 0.05133288, 0.16716792, 0.21575909,
       0.25523658, 0.05506949, 0.04651781, 0.05720362, 0.08030683,
       0.02304245, 0.06157059, 0.05008734, 0.15516822, 0.18601808,
       0.21583504, 0.07200577, 0.0644566 , 0.07830182, 0.09351409]), array([0.00958706, 0.03141753, 0.02604443, 0.14323231, 0.37568824,
       0.23243178, 0.06273243, 0.04210939, 0.03602994, 0.04072688,
       0.02187274, 0.05142478, 0.04684255, 0.1621589 , 0.21491186,
       0.251461  , 0.05971987, 0.05067013, 0.06110843, 0.07982975,
       0.02463173, 0.06076431, 0.04773605, 0.152759  , 0.19549022,
       0.21771915, 0.06746559, 0.06294977, 0.07664815, 0.09383603]), array([0.0119437 , 0.03647622, 0.02778535, 0.13107634, 0.37353941,
       0.22973796, 0.06140853, 0.0440813 , 0.03770739, 0.0462438 ,
       0.02465972, 0.05078231, 0.04720693, 0.14598666, 0.

In [47]:
print(len(lbp_top_vectors[0]))
print(lbp_top_vectors[0])

30
[0.00964533 0.03021189 0.02812334 0.14271284 0.38607124 0.21948811
 0.05827447 0.04540898 0.03890028 0.04116351 0.02334624 0.04805954
 0.05133288 0.16716792 0.21575909 0.25523658 0.05506949 0.04651781
 0.05720362 0.08030683 0.02304245 0.06157059 0.05008734 0.15516822
 0.18601808 0.21583504 0.07200577 0.0644566  0.07830182 0.09351409]
